In [1]:
from bert import tokenization
from bert import optimization
from bert import run_classifier
import bert
import os

os.environ["CUDA_VISIBLE_DEVICES"] = '1'

In [2]:
import h5py
import numpy as np
from pandas import HDFStore, read_hdf
import matplotlib.pyplot as plt
import pandas as pd
from sklearn.model_selection import train_test_split

import nltk
import numpy as np
import tensorflow as tf
import tensorflow_hub as hub
#import seaborn as sns
import csv

np.random.seed(0)
%matplotlib inline

In [3]:
top50data = read_hdf('../Data/ServiceWithName.h5', key='AllData')
top50data.head()

ServiceName                                 ServiceDescription  \
0  Google Maps API  Google Maps' services have been split into mul...   
1      Twitter API  It has been split into multiple APIs, includin...   
2      YouTube API  The Data API allows users to integrate their p...   
3       Flickr API  The Flickr API can be used to retrieve photos ...   
4     Facebook API  Its functions have been split among the follow...   

  ServiceClassification  
0               Mapping  
1                Social  
2                 Video  
3                Photos  
4                Social

In [4]:
top50data.shape

(10943, 3)

In [5]:
top50data['ServiceClassification']

0          Mapping
1           Social
2            Video
3           Photos
4           Social
           ...    
15339     Security
15340        Email
15341        Games
15342    Financial
15343      Medical
Name: ServiceClassification, Length: 10943, dtype: object

In [6]:
top50data[top50data['ServiceClassification'] == 'Social']

ServiceName                                 ServiceDescription  \
1             Twitter API  It has been split into multiple APIs, includin...   
4            Facebook API  Its functions have been split among the follow...   
13         Foursquare API  The Foursquare API provides location based exp...   
23           LinkedIn API  LinkedIn is the world's largest business socia...   
31     Facebook Graph API  From documentation: At Facebook's core is the ...   
...                   ...                                                ...   
15202   Salsa Commons API  The service provides tools for recruiting, fun...   
15243          Subeta API  Subeta is a forum-based social site on which u...   
15244        Tellgram API  Tellgram is a community of people who design w...   
15326     Tweetburner API  Tweetburner is the webservice that lets you sh...   
15328        FindMeOn API  Use the FindMeOn API to manage your identities...   

      ServiceClassification  
1                    Social  
4                    Social  
13                   Social  
23                   Social  
31                   Social  
...                     ...  
15202                Social  
15243                Social  
15244                Social  
15326                Social  
15328                Social  

[433 rows x 3 columns]

#### 加载语料库数据，用于计算TF-IWF

In [7]:
import pickle
  
f = open('../Data/addDataTokenAndIndexCorpus.pickle', 'rb')
corpusTuple = pickle.load(f)
tokenCorpus = corpusTuple[0]
tokenIndexCorpus = corpusTuple[1]
f.close()

### 按照训练集：测试集 = 8：2的比例划分每一个类别的数据，也就是每个类别都有80%在训练集，20%在测试集合

In [8]:
Train = []
Test = []

for c in set(top50data['ServiceClassification']):
    C_data = top50data[top50data['ServiceClassification'] == c]
    C_Train, C_Test = train_test_split(C_data, test_size=0.2, random_state=0)
    Train.append(C_Train)
    Test.append(C_Test)

Train_C = pd.concat(Train)
Test_C = pd.concat(Test)

In [9]:
print(Train_C.shape)
print(Test_C.shape)

(8733, 3)
(2210, 3)


#### TF-IWF算法实现

In [10]:
import math
class TF_IWF:
    '''
    tf-iwf 算法
    '''

    def __init__(self, lines):
        self.iwf = dict()
        self.median_iwf = 0
        self.__build_iwf(lines)

    def __get_tf(self, strs):
        tf_dict = {}
        total_word_line = len(strs)
        for word in strs:
            if word not in tf_dict:
                tf_dict[word] = 1
            else:
                tf_dict[word] = tf_dict[word] + 1
        for k, v in tf_dict.items():
            tf_dict[k] = v / total_word_line
        return tf_dict

    def __build_iwf(self, lines):

        for line in lines:
            for word in line:
                if word not in self.iwf:
                    self.iwf[word] = 1
                else:
                    self.iwf[word] = self.iwf[word] + 1
        total_word_lines = sum(self.iwf.values())
        print(self.iwf.items())
        print(total_word_lines)
        values = []
        for k, v in self.iwf.items():
            self.iwf[k] = math.log(total_word_lines / v, 10)
            values.append(math.log(total_word_lines / v, 10))
        self.median_iwf = np.median(values)

    def get_tfiwf(self, strs):
        result = dict()
        tf_dict = self.__get_tf(strs)
        for word in strs:
            if word not in self.iwf.keys():
                result[word] = tf_dict[word] * self.median_iwf
            else:
                result[word] = tf_dict[word] * self.iwf[word]
        return result

In [11]:
tokenTFIWFClass = TF_IWF(tokenCorpus)
tokenIndexTFIWFClass = TF_IWF(tokenIndexCorpus)

dict_items([('patent', 15), (',', 51715), ('family', 94), ('legal', 69), ('bi', 120), ('##bl', 108), ('##io', 139), ('##graphic', 44), ('data', 9247), ('and', 42849), ('documents', 381), ('available', 3218), ('via', 1518), ('web', 3654), ('service', 6346), ('.', 56050), ('pi', 59), ('##x', 1141), ('##ena', 15), ('##te', 296), ('is', 15873), ('the', 41621), ('photo', 245), ('editor', 55), ('of', 16682), ('choice', 46), ('for', 13445), ('printing', 92), ('sharing', 452), ('businesses', 708), ('related', 557), ('suggestion', 11), ('provides', 5579), ('suggestions', 44), ('que', 310), ('##ries', 297), ('to', 28397), ('submitted', 121), ('query', 514), ('phi', 17), ('##sh', 56), ('##tan', 20), ('##k', 516), ('a', 19975), ('free', 1011), ('community', 369), ('site', 1392), ('where', 378), ('anyone', 87), ('can', 7494), ('submit', 297), ('verify', 160), ('track', 579), ('share', 641), ('##shing', 9), ('allows', 6831), ('developers', 6364), ('make', 715), ('run', 215), ('searches', 148), ('aga

dict_items([(7353, 15), (1010, 51715), (2155, 94), (3423, 69), (12170, 120), (16558, 108), (3695, 139), (14773, 44), (2951, 9247), (1998, 42849), (5491, 381), (2800, 3218), (3081, 1518), (4773, 3654), (2326, 6346), (1012, 56050), (14255, 59), (2595, 1141), (8189, 15), (2618, 296), (2003, 15873), (1996, 41621), (6302, 245), (3559, 55), (1997, 16682), (3601, 46), (2005, 13445), (8021, 92), (6631, 452), (5661, 708), (3141, 557), (10293, 11), (3640, 5579), (15690, 44), (10861, 310), (5134, 297), (2000, 28397), (7864, 121), (23032, 514), (13569, 17), (4095, 56), (5794, 20), (2243, 516), (1037, 19975), (2489, 1011), (2451, 369), (2609, 1392), (2073, 378), (3087, 87), (2064, 7494), (12040, 297), (20410, 160), (2650, 579), (3745, 641), (12227, 9), (4473, 6831), (9797, 6364), (2191, 715), (2448, 215), (17193, 148), (2114, 177), (7668, 6), (2811, 56), (1005, 3814), (3573, 498), (4031, 645), (7809, 1232), (3165, 30), (7138, 40), (11058, 178), (2717, 4203), (8778, 660), (2109, 1485), (2039, 1801),

In [12]:
## shuffle整个数据集
train = Train_C.sample(frac=1)
test = Test_C.sample(frac=1)

# Pepare Data in Mini-batch Set

In [13]:
DATA_COLUMN = 'ServiceDescription'
LABEL_COLUMN = 'ServiceClassification'
# label_list is the list of labels, i.e. True, False or 0, 1 or 'dog', 'cat'
label_list = set(train['ServiceClassification'])

In [14]:
train['ServiceDescriptionLength'] = train['ServiceDescription'].str.len()
train.sort_values('ServiceDescriptionLength', ascending=True, inplace=True)

In [15]:
test['ServiceDescriptionLength'] = test['ServiceDescription'].str.len()
test.sort_values('ServiceDescriptionLength', ascending=True, inplace=True) 

In [16]:
test.iloc[0]['ServiceDescription']

'Patent, family, legal, bibliographic data, and documents available via web service.'

In [17]:
label_list

{'Advertising',
 'Analytics',
 'Application Development',
 'Backend',
 'Banking',
 'Bitcoin',
 'Chat',
 'Cloud',
 'Data',
 'Database',
 'Domains',
 'Education',
 'Email',
 'Enterprise',
 'Entertainment',
 'Events',
 'File Sharing',
 'Financial',
 'Games',
 'Government',
 'Images',
 'Internet of Things',
 'Mapping',
 'Media',
 'Medical',
 'Messaging',
 'Music',
 'News Services',
 'Office',
 'Other',
 'Payments',
 'Photos',
 'Project Management',
 'Real Estate',
 'Reference',
 'Science',
 'Search',
 'Security',
 'Shipping',
 'Social',
 'Sports',
 'Stocks',
 'Storage',
 'Telephony',
 'Tools',
 'Transportation',
 'Travel',
 'Video',
 'Weather',
 'eCommerce'}

In [18]:
 #告诉TF它可以使用每块GPU显存的40%  
config = tf.ConfigProto()
config.gpu_options.per_process_gpu_memory_fraction = 0.2
# session = tf.Session(config=config, ...)

In [19]:
# 从本地的BERT模型中加载词汇表和小写转换器
from absl import flags
import sys

BERT_MODEL_HUB = "../ServeNet/download"

sys.argv = ['preserve_unused_tokens=False']
flags.FLAGS(sys.argv)


def create_tokenizer_from_hub_module():
    """Get the vocab file and casing info from the Hub module."""
    with tf.Graph().as_default():
        bert_module = hub.Module(BERT_MODEL_HUB)
        tokenization_info = bert_module(signature="tokenization_info",
                                        as_dict=True)
        with tf.Session(config=config) as sess:
            vocab_file, do_lower_case = sess.run([
                tokenization_info["vocab_file"],
                tokenization_info["do_lower_case"]
            ])

    return bert.tokenization.FullTokenizer(vocab_file=vocab_file,
                                           do_lower_case=do_lower_case)


tokenizer = create_tokenizer_from_hub_module()

INFO:tensorflow:Saver not created because there are no variables in the graph to restore


In [20]:
tokenizer.tokenize("Patent, family, legal, bibliographic data, and documents available via web service.")

['patent',
 ',',
 'family',
 ',',
 'legal',
 ',',
 'bi',
 '##bl',
 '##io',
 '##graphic',
 'data',
 ',',
 'and',
 'documents',
 'available',
 'via',
 'web',
 'service',
 '.']

In [21]:
# 这一部分是用来测试数据类型的,不需要运行
def test_MiniBatch(data,
                   batchsize=32,
                   maxDesLength=110,
                   maxNameLength=10):

    returnData = []
    for i, g in data.groupby(np.arange(len(data)) // batchsize):
        # ----------------------------------------------获取服务描述的inputExample----------------------------
        # 32个bert.run_classifier.InputExample组成一个pandas.core.series.Series的ServiceDes_InputExamples
        ServiceDes_InputExamples = g.apply(
            lambda x: bert.run_classifier.InputExample(guid=None,
                                                       text_a=x['ServiceDescription'],
                                                       text_b=None,
                                                       label=x[LABEL_COLUMN]),
            axis=1)
        maxLengthInMiniBatch = len(ServiceDes_InputExamples.iloc[-1].text_a)
        print("MiniBatch MaxLength: " + str(maxLengthInMiniBatch))
        if maxLengthInMiniBatch >= maxDesLength:
            # 把数据转换为BERT理解的格式，[input_id,input_mask,input_segment]
            serviceDes_features = bert.run_classifier.convert_examples_to_features(
                ServiceDes_InputExamples, label_list, maxDesLength, tokenizer)
        else:
            # 否则把服务描述最大长度设定为该批数据的最大长度
            # -----------数据类型为bert.run_classifier.InputFeatures----------------------------
            # serviceDes_features的数据类型是列表,不再是Series
            serviceDes_features = bert.run_classifier.convert_examples_to_features(
                ServiceDes_InputExamples, label_list, maxLengthInMiniBatch,
                tokenizer)
            # ----------------------------------------------获取服务描述的分词结果----------------------------
        ServiceDes_token = g.apply(
            lambda x: tokenizer.tokenize(x['ServiceDescription']), axis=1)
        returnData.append(serviceDes_features)

    return returnData
list = test_MiniBatch(test)
type(list)
type(list[0]) # 代表每一批次数据
for (index,example) in enumerate(list[0]):
    print(index)
    print(example)
type(list[0].iloc[0])
list[0].iloc[0]
list[0].iloc[0].text_a #每一批次数据的第0行是一个bert.run_classifier.InputExample

MiniBatch MaxLength: 168
INFO:tensorflow:Writing example 0 of 32
INFO:tensorflow:*** Example ***
INFO:tensorflow:guid: None
INFO:tensorflow:tokens: [CLS] patent , family , legal , bi ##bl ##io ##graphic data , and documents available via web service . [SEP]
INFO:tensorflow:input_ids: 101 7353 1010 2155 1010 3423 1010 12170 16558 3695 14773 2951 1010 1998 5491 2800 3081 4773 2326 1012 102 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:tensorflow:input_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:tensorflow:segment_ids: 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 

INFO:tensorflow:input_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:tensorflow:segment_ids: 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:tensorflow:label: Security (id = 34)
INFO:tensorflow:*** Example ***
INFO:tensorflow:guid: None
INFO:tensorflow:tokens: [CLS] batch ##book is an easy - to - use customer relationship manager ( cr ##m ) designed for small business owners . the batch ##book api is an xml rest interface for access ##ing your account . [SEP]
INFO:tensorflow:input_ids: 101 14108 8654 2003 2019 3733 1011 2000 1011 2224 8013 3276 3208 1006 13675 2213 1007 2881 2005 2235 2449 5608 1012 1996 14108 8654 17928 2003 2019 

INFO:tensorflow:input_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:tensorflow:segment_ids: 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:tensorflow:label: Education (id = 9)
MiniBatch MaxLength: 238
INFO:tensorflow:Writing example 0 of 32
INFO:tensorflow:*** Example ***
INFO:tensorflow:guid: None
INFO:tensorflow:tokens: [CLS] this rest api allows apps to store custom data in a message , event , or contact of the user ' s account . the account can be on office 365 or microsoft and includes ; hot ##mail . com , live . com , ms ##n . com , outlook . com and passport . com . [SEP]
INFO:tensorflow:input_ids: 101 2023 2717 17928 4473

INFO:tensorflow:segment_ids: 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:tensorflow:label: Messaging (id = 19)
INFO:tensorflow:*** Example ***
INFO:tensorflow:guid: None
INFO:tensorflow:tokens: [CLS] the pl ##ivo call request api allows developers to perform actions on a call request , before the call is answered . pl ##ivo is a carrier service company that provides businesses a way to communicate with their customers via sms and voice calls . [SEP]
INFO:tensorflow:input_ids: 101 1996 20228 20984 2655 5227 17928 4473 9797 2000 4685 4506 2006 1037 2655 5227 1010 2077 1996 2655 2003 4660 1012 20228 20984 2003 1037 6839 2326 2194 2008 3640 5661 1037 2126 2000 10639 2007 2037 6304 3081 22434 1998 2376 4455 1012 102 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 

INFO:tensorflow:*** Example ***
INFO:tensorflow:guid: None
INFO:tensorflow:tokens: [CLS] emerge ##nt one is an api building , creation , and management platform . customers can build and create their api ##s with emerge ##nt one . emerge ##nt one offers developers a development portal , with api documentation , api analytics , and api management services . [SEP]
INFO:tensorflow:input_ids: 101 12636 3372 2028 2003 2019 17928 2311 1010 4325 1010 1998 2968 4132 1012 6304 2064 3857 1998 3443 2037 17928 2015 2007 12636 3372 2028 1012 12636 3372 2028 4107 9797 1037 2458 9445 1010 2007 17928 12653 1010 17928 25095 1010 1998 17928 2968 2578 1012 102 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:tensorflow:input_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 

...

INFO:tensorflow:input_ids: 101 2951 18938 3258 20192 24658 17928 2015 9585 9797 2000 3443 7300 2005 2729 12016 1998 2060 3791 2008 28999 3863 4816 2740 2636 1999 1039 1011 3729 2050 4289 1998 2060 4127 1997 5491 3081 3622 5851 24732 1998 4372 26775 22571 3064 10373 1012 2478 2951 18938 3258 20192 24658 17928 2015 1010 5097 2064 4685 1037 5041 2846 1997 8518 2107 2004 6016 1998 4909 5491 1010 6575 2083 1996 9871 10802 14176 1006 6522 2094 1007 1010 9347 2075 1998 28965 5310 6115 1010 4488 4767 27354 2005 5776 10316 1998 2500 1012 2951 18938 3258 20192 24658 17928 2015 2024 3253 2004 7815 102
INFO:tensorflow:input_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1
INFO:tensorflow:segment_ids: 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0

INFO:tensorflow:label: Telephony (id = 36)
INFO:tensorflow:*** Example ***
INFO:tensorflow:guid: None
INFO:tensorflow:tokens: [CLS] the service from the national library of australia provides search access to catalog records and other descriptive metadata for a wide range of resources : books , periodicals ( e . g . , journal articles and newspaper articles ) , images , maps , music and video recordings , and archives of physical objects . the service can also return user - created lists of web links . future development may provide lists of people and organizations . results for newspaper articles give access to full text for digital versions . api methods support submission of search que ##ries , including filtering parameters such as title - [SEP]
INFO:tensorflow:input_ids: 101 1996 2326 2013 1996 2120 3075 1997 2660 3640 3945 3229 2000 12105 2636 1998 2060 22726 27425 2005 1037 2898 2846 1997 4219 1024 2808 1010 21855 1006 1041 1012 1043 1012 1010 3485 4790 1998 3780 4790 1007 1010

INFO:tensorflow:input_ids: 101 1996 9353 15549 2050 6336 5245 17928 4473 2017 2000 4374 2592 1999 2613 2051 2043 1037 10367 2000 2115 4037 8039 1037 6903 1999 2029 2017 1005 2128 3391 4699 1012 1996 26828 7696 2008 1996 9353 15549 2050 6336 2326 10255 2000 2019 8299 8241 2097 5383 1996 2206 11709 1024 2711 1010 3543 1010 2724 1998 2062 1012 2074 4607 1037 24471 2140 1998 5482 3563 9214 2000 1996 3295 1010 2061 2008 7188 1037 2711 8039 3327 9214 1010 1037 26828 4820 2592 2055 1996 2711 1010 3543 1010 2724 1998 10349 9214 2003 2741 2000 1996 24471 2140 2008 2017 2031 4217 1012 102
INFO:tensorflow:input_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1
INFO:tensorflow:segment_ids: 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0

INFO:tensorflow:label: Transportation (id = 38)
INFO:tensorflow:*** Example ***
INFO:tensorflow:guid: None
INFO:tensorflow:tokens: [CLS] opens ##tree ##tma ##p is the free wi ##ki world map , an open volunteer - driven initiative to collaborative ##ly create a map of the world , and release the map data under a free and open license . there are actually many different api ##s in and around the opens ##tree ##tma ##p ecosystem . many developers searching for an api , may actually be looking for an java ##script web mapping library . there are a few of these to choose from including free and open source options such as leaf ##let ##js . these work by fetch ##ing map tiles from a tile server [SEP]
INFO:tensorflow:input_ids: 101 7480 13334 29418 2361 2003 1996 2489 15536 3211 2088 4949 1010 2019 2330 6951 1011 5533 6349 2000 12317 2135 3443 1037 4949 1997 1996 2088 1010 1998 2713 1996 4949 2951 2104 1037 2489 1998 2330 6105 1012 2045 2024 2941 2116 2367 17928 2015 1999 1998 2105 1996 7480 

AttributeError: 'list' object has no attribute 'iloc'

In [22]:
def convert_to_one_hot(Y, C):
    Y = np.eye(C)[Y.reshape(-1)]
    return Y

In [23]:
# 这个函数用来把文本长度超过108的进行截断，只保留前108，然后返回截断后的分词结果
def MaxLengthAndToken(inputlist):
    if(len(inputlist) > 108):
        inputlist = inputlist[0:108]
    return tokenizer.convert_tokens_to_ids(inputlist)

In [24]:
# allDataToken = []  # 用来计算corpus语料库
# allDataTokenIndex = []  # 用来保存每个批次数据转换为索引后的数值


def prepareData_BERT_MiniBatch(data,
                               batchsize=32,
                               maxDesLength=110,
                               maxNameLength=10):

    returnData = []
    for i, g in data.groupby(np.arange(len(data)) // batchsize):
        # ----------------------------------------------获取服务描述的inputExample----------------------------
        ServiceDes_InputExamples = g.apply(
            lambda x: bert.run_classifier.InputExample(guid=None,
                                                       text_a=x['ServiceDescription'],
                                                       text_b=None,
                                                       label=x[LABEL_COLUMN]),
            axis=1)
        maxLengthInMiniBatch = len(ServiceDes_InputExamples.iloc[-1].text_a)
        print("MiniBatch MaxLength: " + str(maxLengthInMiniBatch))
        # ----------------------------------------------获取服务名称的inputExample----------------------------
        serviceName_InputExamples = g.apply(
            lambda x: bert.run_classifier.InputExample(guid=None,
                                                       text_a=x['ServiceName'],
                                                       text_b=None,
                                                       label=x[LABEL_COLUMN]),
            axis=1)

        # ----------------------------------------------获取服务描述的分词结果----------------------------
        ServiceDes_token = g.apply(
            lambda x: tokenizer.tokenize(x['ServiceDescription']), axis=1)
        # allDataToken.append(ServiceDes_token)
        # ----------------------------------------------获取服务描述的分词后的索引结果----------------------------
        ServiceDes_token_index = ServiceDes_token.apply(
            lambda x: MaxLengthAndToken(x))
        # ----------------------------------------------获取服务描述的分词后的TF-IWF值--------------
        ServiceDes_token_index_TFIWF = ServiceDes_token_index.apply(
            lambda x: tokenIndexTFIWFClass.get_tfiwf(x))
        # allDataTokenIndex.append(ServiceDes_token_index)

        # ----------------------------------------------获取服务名称的分词结果----------------------------
        ServiceName_token = g.apply(
            lambda x: tokenizer.tokenize(x['ServiceName']), axis=1)
        # --------------------------------------------获取服务描述的 id mask segment--------------------------
#         if maxLengthInMiniBatch >= maxDesLength:
#             # 把数据转换为BERT理解的格式，[input_id,input_mask,input_segment]
        serviceDes_features = bert.run_classifier.convert_examples_to_features(
            ServiceDes_InputExamples, label_list, maxDesLength, tokenizer)
#         else:
#             # 否则把服务描述最大长度设定为该批数据的最大长度
#             serviceDes_features = bert.run_classifier.convert_examples_to_features(
#                 ServiceDes_InputExamples, label_list, maxLengthInMiniBatch,
#                 tokenizer)
        # --------------------------------------------获取服务名称的 id mask segment--------------------------
        # serviceName_features的数据类型是列表,不再是Series
        serviceName_features = bert.run_classifier.convert_examples_to_features(
            serviceName_InputExamples, label_list, maxNameLength, tokenizer)
        # --------------------------------------------把id mask segment组织成批数据存储------------------------
        des_input_id = np.array([o.input_ids for o in serviceDes_features])
        des_input_mask = np.array([o.input_mask for o in serviceDes_features])
        des_input_segment = np.array(
            [o.segment_ids for o in serviceDes_features])

        name_input_id = np.array([o.input_ids for o in serviceName_features])
        name_input_mask = np.array(
            [o.input_mask for o in serviceName_features])
        name_input_segment = np.array(
            [o.segment_ids for o in serviceName_features])
        # ---------------------------------------------把服务标签组织成批数据存储--------------------------------
        input_label = np.array([o.label_id for o in serviceName_features])
        input_label_one_hot = convert_to_one_hot(input_label, 50)
        # ---------------------------------------------把分词后的结果存入DataFrame--------------------------------
        # ------------------------ServiceName_token是Series类型,因为是直接对g进行操作
        # ------------------------ServiceDes_token也是Series类型,因为是直接对g进行操作
        # ------------------------serviceName_features和serviceDes_features是List嵌套的类型
        g['serviceNameToken'] = ServiceName_token
        g['ServiceDesToken'] = ServiceDes_token
        g['ServiceDes_token_index'] = ServiceDes_token_index
        g['ServiceDes_token_index_TFIWF'] = ServiceDes_token_index_TFIWF
        # --------------------------最终返回的数据是一个三元组，DataFrame、BERT input，Label_one_hot----------------
        data_MiniBatch = g, [
            des_input_id, des_input_mask, des_input_segment, name_input_id,
            name_input_mask, name_input_segment
        ], input_label_one_hot
        returnData.append(data_MiniBatch)

    return returnData

In [25]:
testdata = prepareData_BERT_MiniBatch(test, batchsize = 32) 
traindata = prepareData_BERT_MiniBatch(train, batchsize = 32) 

MiniBatch MaxLength: 168
INFO:tensorflow:Writing example 0 of 32
INFO:tensorflow:*** Example ***
INFO:tensorflow:guid: None
INFO:tensorflow:tokens: [CLS] patent , family , legal , bi ##bl ##io ##graphic data , and documents available via web service . [SEP]
INFO:tensorflow:input_ids: 101 7353 1010 2155 1010 3423 1010 12170 16558 3695 14773 2951 1010 1998 5491 2800 3081 4773 2326 1012 102 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:tensorflow:input_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:tensorflow:segment_ids: 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 

INFO:tensorflow:guid: None
INFO:tensorflow:tokens: [CLS] path of exile is an online action fantasy rpg from grinding gear games . the path of exile api expose ##s game metadata describing leagues , league rules , and player ratings . [SEP]
INFO:tensorflow:input_ids: 101 4130 1997 8340 2003 2019 3784 2895 5913 22531 2013 16153 6718 2399 1012 1996 4130 1997 8340 17928 14451 2015 2208 27425 7851 8121 1010 2223 3513 1010 1998 2447 8599 1012 102 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:tensorflow:input_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:tensorflow:segment_ids: 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 

INFO:tensorflow:input_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:tensorflow:segment_ids: 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:tensorflow:label: Images (id = 2)
INFO:tensorflow:*** Example ***
INFO:tensorflow:guid: None
INFO:tensorflow:tokens: [CLS] real ##ty ##bar ##on ' s agents api is a free service that enables websites or mobile apps to quickly offer ' find an agent ' services to both consumers and professionals with minimal integration and zero administration . [SEP]
INFO:tensorflow:input_ids: 101 2613 3723 8237 2239 1005 1055 6074 17928 2003 1037 2489 2326 2008 12939 11744 2030 4684 18726 2000 2855 3749 1005 24

INFO:tensorflow:segment_ids: 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:tensorflow:label: Social (id = 22)
INFO:tensorflow:*** Example ***
INFO:tensorflow:guid: None
INFO:tensorflow:tokens: [CLS] the z ##ype api integrate ##s video features into applications , aiming to convert fans into customers . it is available in j ##son and xml architecture ##s with a rest ##ful api service . z ##ype is an ot ##t ( over the top content ) video platform . [SEP]
INFO:tensorflow:input_ids: 101 1996 1062 18863 17928 17409 2015 2678 2838 2046 5097 1010 13659 2000 10463 4599 2046 6304 1012 2009 2003 2800 1999 1046 3385 1998 20950 4294 2015 2007 1037 2717 3993 17928 2326 1012 1062 18863 2003 2019 27178 2102 1006 2058 1996 2327 4180 1007 2678 4132 1012 102 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 

INFO:tensorflow:segment_ids: 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:tensorflow:label: Telephony (id = 36)
INFO:tensorflow:*** Example ***
INFO:tensorflow:guid: None
INFO:tensorflow:tokens: [CLS] the ins ##tar ##em api allows developers to access and integrate the functionality of ins ##tar ##em with other applications . public documentation is not available ; api access comes with account service . ins ##tar ##em is a money transfer platform in asia . [SEP]
INFO:tensorflow:input_ids: 101 1996 16021 7559 6633 17928 4473 9797 2000 3229 1998 17409 1996 15380 1997 16021 7559 6633 2007 2060 5097 1012 2270 12653 2003 2025 2800 1025 17928 3229 3310 2007 4070 2326 1012 16021 7559 6633 2003 1037 2769 4651 4132 1999 4021 1012 102 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 

...

INFO:tensorflow:label: Cloud (id = 48)
INFO:tensorflow:Writing example 0 of 32
INFO:tensorflow:*** Example ***
INFO:tensorflow:guid: None
INFO:tensorflow:tokens: [CLS] int ##rini ##o dominican republic stock exchange prices [SEP]
INFO:tensorflow:input_ids: 101 20014 22612 2080 10104 3072 4518 3863 7597 102
INFO:tensorflow:input_mask: 1 1 1 1 1 1 1 1 1 1
INFO:tensorflow:segment_ids: 0 0 0 0 0 0 0 0 0 0
INFO:tensorflow:label: Stocks (id = 5)
INFO:tensorflow:*** Example ***
INFO:tensorflow:guid: None
INFO:tensorflow:tokens: [CLS] federal ##re ##gist ##er . gov api [SEP]
INFO:tensorflow:input_ids: 101 2976 2890 24063 2121 1012 18079 17928 102 0
INFO:tensorflow:input_mask: 1 1 1 1 1 1 1 1 1 0
INFO:tensorflow:segment_ids: 0 0 0 0 0 0 0 0 0 0
INFO:tensorflow:label: Government (id = 49)
INFO:tensorflow:*** Example ***
INFO:tensorflow:guid: None
INFO:tensorflow:tokens: [CLS] vi ##dm ##e api [SEP]
INFO:tensorflow:input_ids: 101 6819 22117 2063 17928 102 0 0 0 0
INFO:tensorflow:input_mask: 1 1 1 

INFO:tensorflow:input_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1
INFO:tensorflow:segment_ids: 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
INFO:tensorflow:label: Messaging (id = 19)
INFO:tensorflow:*** Example ***
INFO:tensorflow:guid: None
INFO:tensorflow:tokens: [CLS] catch ##point provides active web performance monitoring from multiple locations around the world . the catch ##point solution is a tool that helps in identifying and resolving performance and availability issues before they affect end users . the solution allows users to monitor not only performance of http and https , but also that of d ##ns , tc ##p , ft ##p , and m

INFO:tensorflow:input_ids: 101 1996 2729 2102 17928 11082 5198 17445 2037 6047 5080 13907 1998 6970 8663 2638 6593 2068 2007 2353 2283 5733 1004 5097 2000 8285 8585 7661 21335 3468 3570 6631 2578 1012 5198 2064 3745 2054 2027 2024 2725 1999 2028 10439 2043 2027 2024 2725 2009 3081 2019 9123 2729 2102 3570 1012 2115 3570 2071 8073 2689 2043 2017 2707 2652 1037 2208 1998 5383 1037 4957 1010 6302 1998 2062 2055 2008 2208 1012 2005 2062 3375 2892 1011 10439 2030 13617 13330 3570 2229 1010 2017 2064 2344 7661 2328 7300 2083 2729 2102 1005 1055 4773 4012 23041 5555 4263 2007 1996 102
INFO:tensorflow:input_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1
INFO:tensorflow:segment_ids: 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 

INFO:tensorflow:label: Messaging (id = 19)
INFO:tensorflow:*** Example ***
INFO:tensorflow:guid: None
INFO:tensorflow:tokens: [CLS] the hellenic bank single payment in rub ##les api allows you to make single payments within hellenic bank as well as swift payments . with this api , payments may only be made in rub ##les . transactions are performed in a secure manner with the o ##au ##th 2 protocol . self - register to get started . testing for your your app is available in hellenic bank is sand ##box environment . real - time access on account activity via the sand ##box log . hellenic bank offers a platform of financial api ##s . companies or developers interested in using the api ##s can register [SEP]
INFO:tensorflow:input_ids: 101 1996 23122 2924 2309 7909 1999 14548 4244 17928 4473 2017 2000 2191 2309 10504 2306 23122 2924 2004 2092 2004 9170 10504 1012 2007 2023 17928 1010 10504 2089 2069 2022 2081 1999 14548 4244 1012 11817 2024 2864 1999 1037 5851 5450 2007 1996 1051 4887 2705 

INFO:tensorflow:label: Travel (id = 29)
INFO:tensorflow:*** Example ***
INFO:tensorflow:guid: None
INFO:tensorflow:tokens: [CLS] e ##bay api [SEP]
INFO:tensorflow:input_ids: 101 1041 15907 17928 102 0 0 0 0 0
INFO:tensorflow:input_mask: 1 1 1 1 1 0 0 0 0 0
INFO:tensorflow:segment_ids: 0 0 0 0 0 0 0 0 0 0
INFO:tensorflow:label: Search (id = 43)
INFO:tensorflow:*** Example ***
INFO:tensorflow:guid: None
INFO:tensorflow:tokens: [CLS] hellenic bank single payment api [SEP]
INFO:tensorflow:input_ids: 101 23122 2924 2309 7909 17928 102 0 0 0
INFO:tensorflow:input_mask: 1 1 1 1 1 1 1 0 0 0
INFO:tensorflow:segment_ids: 0 0 0 0 0 0 0 0 0 0
INFO:tensorflow:label: Payments (id = 11)


In [26]:
print(len(testdata))
print(len(traindata))

70
273


In [36]:
traindata[0][1][0].shape

(32, 110)

#### 把数据存储起来，先存储token语料库，再存储tokenid语料库

In [160]:
corpus = (tokenCorpus,indexcorpus)
import pickle
  
f = open('../Data/addDataTokenAndIndexCorpus.pickle', 'wb')
pickle.dump(corpus, f)
f.close()

In [3]:
import pickle
  
f = open('../Data/addDataTokenAndIndexCorpus.pickle', 'rb')
corpusTuple = pickle.load(f)
f.close()

In [23]:
corpusTuple[0]

[['patent',
  ',',
  'family',
  ',',
  'legal',
  ',',
  'bi',
  '##bl',
  '##io',
  '##graphic',
  'data',
  ',',
  'and',
  'documents',
  'available',
  'via',
  'web',
  'service',
  '.'],
 ['pi',
  '##x',
  '##ena',
  '##te',
  'is',
  'the',
  'photo',
  'editor',
  'of',
  'choice',
  'for',
  'photo',
  'printing',
  'and',
  'photo',
  'sharing',
  'businesses',
  '.'],
 ['the',
  'related',
  'suggestion',
  'service',
  'provides',
  'suggestions',
  'for',
  'que',
  '##ries',
  'related',
  'to',
  'the',
  'submitted',
  'query',
  '.'],
 ['phi',
  '##sh',
  '##tan',
  '##k',
  'is',
  'a',
  'free',
  'community',
  'site',
  'where',
  'anyone',
  'can',
  'submit',
  ',',
  'verify',
  ',',
  'track',
  'and',
  'share',
  'phi',
  '##shing',
  'data',
  '.'],
 ['allows',
  'developers',
  'to',
  'make',
  'que',
  '##ries',
  'and',
  'run',
  'searches',
  'against',
  'cafe',
  'press',
  "'",
  'store',
  'and',
  'product',
  'database',
  '.'],
 ['the',
  'silv

In [7]:
len(corpusTuple[1])

13153

In [37]:
import pickle
  
f = open('../Data/BERT-ServiceDatasetWithNameMiniBatch-TestData.pickle', 'wb')
pickle.dump(testdata, f)
f.close()

In [38]:
import pickle

f = open('../Data/BERT-ServiceDatasetWithNameMiniBatch-TestData.pickle', 'rb')
testloaded = pickle.load(f)
f.close()

In [41]:
testloaded[0][0]['ServiceDes_token_index']

1357     [7353, 1010, 2155, 1010, 3423, 1010, 12170, 16...
14812    [14255, 2595, 8189, 2618, 2003, 1996, 6302, 35...
147      [1996, 3141, 10293, 2326, 3640, 15690, 2005, 1...
444      [13569, 4095, 5794, 2243, 2003, 1037, 2489, 24...
192      [4473, 9797, 2000, 2191, 10861, 5134, 1998, 24...
243      [1996, 3165, 7138, 11058, 2326, 2717, 8778, 20...
14562    [26726, 16700, 2099, 4107, 4684, 10961, 9651, ...
4765     [1996, 1055, 13542, 2545, 2865, 17181, 17928, ...
1201     [2013, 4261, 5332, 16989, 4877, 1012, 3409, 10...
14708    [17928, 2005, 4526, 2460, 24471, 4877, 1012, 2...
14832    [4604, 3793, 7696, 1006, 22434, 1007, 1010, 11...
240      [2007, 2026, 6767, 2595, 1010, 2017, 2064, 237...
96       [12040, 1037, 2299, 2017, 2066, 2000, 1996, 21...
358      [12610, 7159, 2490, 1016, 17928, 2015, 1024, 1...
5304     [1996, 5884, 11343, 4638, 2121, 17928, 2015, 1...
5014     [1996, 2088, 4633, 3784, 2334, 2103, 4633, 179...
8107     [11867, 5596, 24333, 6322, 17928, 4473, 5198, .

#### 输入是列表，格式如下des_input_id, des_input_mask, des_input_segment, name_input_id,name_input_mask, name_input_segment

In [42]:
testloaded[0][1][0][0]

array([  101,  7353,  1010,  2155,  1010,  3423,  1010, 12170, 16558,
        3695, 14773,  2951,  1010,  1998,  5491,  2800,  3081,  4773,
        2326,  1012,   102,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0])

In [43]:
import pickle
  
f = open('../Data/BERT-ServiceDatasetWithNameMiniBatch-TrainData.pickle', 'wb')
pickle.dump(traindata, f)
f.close()

In [44]:
import pickle

f = open('../Data/BERT-ServiceDatasetWithNameMiniBatch-TrainData.pickle', 'rb')
traindataLoaded = pickle.load(f)
f.close()